![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS - S 2019 Pré-natal - Parte 4

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(tictoc)
library(foreign)
library(forcats)
library(tidyverse)
source("utils.R")

## Carregando microdados da PNS

In [2]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2019>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2019>")

[1] 293726   1087

## Definição do peso e filtragem de respondentes do questionário

In [3]:
#Selecionando registros válidos e calculando peso amostral - summary de verificação
pns2019.1<-  <Coloque aqui o nome do arquivo RDATA>  %>% filter(V0025A==1) 
pns2019.1<-pns2019.1 %>% mutate(peso_morador_selec=((V00291*(90846/168426190))))
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2019.1$peso_morador_selec)

    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
 0.00562  0.26621  0.54401  1.00000  1.12765 61.09981 

## Criação de variáveis dos indicadores

In [4]:
#Desfechos - Indicadores

# 16. Proporção de mulheres que fizeram teste de HIV/AIDS durante o pré-natal - S016P.
pns2019.1$S016P <- NA
pns2019.1$S016P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S016P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & pns2019.1$S091==1] <- 1
pns2019.1$S016P<-factor(pns2019.1$S016P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S016P)

# 17. Proporção de mulheres que fizeram teste de HIV/AIDS durante o pré-natal e receberam o resultado antes do parto - S017P.
pns2019.1$S017P <- NA
pns2019.1$S017P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S017P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & pns2019.1$S092==1] <- 1
pns2019.1$S017P<-factor(pns2019.1$S017P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S017P)

# 18. Proporção de mulheres que receberam indicação da maternidade para o parto durante o pré-natal - S018P.
pns2019.1$S018P <- NA
pns2019.1$S018P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S018P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & pns2019.1$S097==1] <- 1
pns2019.1$S018P<-factor(pns2019.1$S018P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S018P)

# 19. Proporção de mulheres que foram atendidas por médico no último parto - S019P.
pns2019.1$S019P <- NA
pns2019.1$S019P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068>0] <- 2
pns2019.1$S019P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068>0 & pns2019.1$S111==1] <- 1
pns2019.1$S019P<-factor(pns2019.1$S019P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S019P)

Sim   Não  NA's 
 2399   335 88112

Sim   Não  NA's 
 2356   378 88112

Sim   Não  NA's 
 2179   555 88112

Sim   Não  NA's 
 2424   394 88028

## Definições de abrangências

### Situação urbana ou rural

In [5]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(urb_rur=V0026)
pns2019.1$urb_rur<-factor(pns2019.1$urb_rur, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2019.1$urb_rur)

urbano  rural 
 69873  20973

### UF

In [6]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(uf=V0001)
pns2019.1$uf<-factor(pns2019.1$uf, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2019.1$uf)

Rondônia                Acre            Amazonas             Roraima 
               2176                2380                3479                2238 
               Pará               Amapá           Tocantins            Maranhão 
               3853                1554                1922                5080 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               2740                4265                2962                3158 
         Pernambuco             Alagoas             Sergipe               Bahia 
               4083                2987                2610                3659 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               5209                3541                4966                6114 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3967                3738                3767                2863 
        Mato Grosso               Goiás    Distrito Federal 
               2468                2702                2365

### Grandes Regiões

In [7]:
#Grandes Regiões
pns2019.1 <- pns2019.1 %>% 
  mutate(região = fct_collapse(uf, 
                                  `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                  `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                  `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                  `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                  `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal"))
        )
summary(pns2019.1$região)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       17602        31544        19830        11472        10398

### Capital

In [8]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(capital= fct_collapse(uf,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2019.1$capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          2176           2380           3479           2238           3853 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1554           1922           5080           2740           4265 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          2962           3158           4083           2987           2610 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          3659           5209           3541           4966           6114 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3967           3738           3767           2863           2468 
       Goiânia       Brasília 
          2702           2365

### Faixa Etária

In [9]:
#Faixas Etárias

pns2019.1 <- pns2019.1 %>% mutate(fx_idade_S=cut(C008,
  breaks = c(18,25,30,40,120),
  labels = c("18 a 24 anos", "25 a 29 anos", "30 a 39 anos", "40 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2019.1$fx_idade_S)

18 a 24 anos    25 a 29 anos    30 a 39 anos 40 anos ou mais            NA's 
           8145            7249           18150           54987            2315

### Raça

In [10]:
#Raça
pns2019.1 <- pns2019.1 %>% mutate(raça= ifelse(C009==1, 1, 
                                               ifelse(C009==2, 2, 
                                                      ifelse(C009==4, 3, 9))))
pns2019.1$raça<-factor(pns2019.1$raça, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))
summary(pns2019.1$raça)

Branca  Preta  Parda   NA's 
 33133  10345  45994   1374

### Renda per capita

In [11]:
#Rendimento domiciliar per capita
pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4, 
                        ifelse(is.na(VDF004)==TRUE, NA_real_, 5))))))
pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM",
                                                                                   "2 até 3 SM","Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)

Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       23697        26406        22466         7612        10643           22

### Escolaridade

In [12]:
# Escolaridade
pns2019.1 <- pns2019.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2019.1$gescol<-factor(pns2019.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))
summary(pns2019.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                36276                                 13520 
   Superior incompleto ou equivalente                     Superior completo 
                                27433                                 13617

## Criando indicadores

### Filtrando base de indicadores

In [13]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2019Ssurvey<- pns2019.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "C008", "C006", "C009", "V0031", 
                                      "urb_rur", "uf", "região",  "capital", "fx_idade_S", "raça", "rend_per_capita", "gescol",
                                      "S016P", "S017P", "S018P", "S019P", "S068") 
summary(pns2019Ssurvey)

     V0024            UPA_PNS      peso_morador_selec      C008       
 1210010: 1167   140001681:   18   Min.   : 0.00562   Min.   : 15.00  
 1410011:  792   140003815:   18   1st Qu.: 0.26621   1st Qu.: 32.00  
 2710111:  779   140005777:   18   Median : 0.54401   Median : 45.00  
 2410011:  745   140006746:   18   Mean   : 1.00000   Mean   : 46.39  
 5010011:  738   140007081:   18   3rd Qu.: 1.12765   3rd Qu.: 60.00  
 3210011:  711   140007715:   18   Max.   :61.09981   Max.   :107.00  
 (Other):85914   (Other)  :90738                                      
      C006            C009           V0031         urb_rur     
 Min.   :1.000   Min.   :1.000   Min.   :1.000   urbano:69873  
 1st Qu.:1.000   1st Qu.:1.000   1st Qu.:1.000   rural :20973  
 Median :2.000   Median :4.000   Median :2.000                 
 Mean   :1.529   Mean   :2.679   Mean   :2.605                 
 3rd Qu.:2.000   3rd Qu.:4.000   3rd Qu.:4.000                 
 Max.   :2.000   Max.   :9.000   Max.   :4.000  

### Exporta tabela filtrada com os dados específicos - Módulo S - Parte 4 2019

In [14]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2019Ssurvey, file.path(diretorio_saida, "pns2019Ssurvey.csv"))

### Cria plano amostral complexo

In [15]:
desPNS=svydesign(id=~UPA_PNS, 
                 strat=~V0024,
                 weight=~peso_morador_selec,
                 nest=TRUE, 
                 data=pns2019Ssurvey)

In [16]:
#survey design S016P a S018P
desPNSS=subset(desPNS, C006==2 & C008>=18 & S068==1)
desPNSS_C=subset(desPNS, C006==2 & C008>=18 & S068==1 & V0031==1)
desPNSS_R=subset(desPNS, C006==2 & C008>=18 & S068==1 & !is.na(raça))
desPNSS_Rend=subset(desPNS, C006==2 & C008>=18 & S068==1 & !is.na(rend_per_capita))

In [17]:
#survey design S019P
desPNSS_S019P=subset(desPNS, C006==2 & C008>=18 & S068>0)
desPNSS_S019P_C=subset(desPNS, C006==2 & C008>=18 & S068>0 & V0031==1)
desPNSS_S019P_R=subset(desPNS, C006==2 & C008>=18 & S068>0 & !is.na(raça))
desPNSS_S019P_Rend=subset(desPNS, C006==2 & C008>=18 & S068>0 & !is.na(rend_per_capita))

#### Definição de variáveis para iteração dos indicadores

In [18]:
design_por_abrangencia <- list(
    S016P = list(
        capital = desPNSS_C,
        raça = desPNSS_R,
        rend_per_capita = desPNSS_Rend,
        default = desPNSS
    ),
    S017P = list(
        capital = desPNSS_C,
        raça = desPNSS_R,
        rend_per_capita = desPNSS_Rend,
        default = desPNSS
    ),
    S018P = list(
        capital = desPNSS_C,
        raça = desPNSS_R,
        rend_per_capita = desPNSS_Rend,
        default = desPNSS
    ),
    S019P = list(
        capital = desPNSS_S019P_C,
        raça = desPNSS_S019P_R,
        rend_per_capita = desPNSS_S019P_Rend,
        default = desPNSS_S019P
    )
)
dominios <- c(
    ~raça,
    ~rend_per_capita,
    ~fx_idade_S,
    ~urb_rur,
    ~uf,
    ~região,
    ~capital,
    ~gescol
) 
indicadores <- c(~S016P, ~S017P, ~S018P, ~S019P)
totais <- c(~Brasil,~Capital)
Ano <- "2019"

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [19]:
matriz_indicadores <- popula_indicadores(design_por_abrangencia, dominios, indicadores, Ano)

In [20]:
matriz_indicadores

abr_tipo       
Branca                                 raça           
Preta                                  raça           
Parda                                  raça           
Até 1/2 SM                             rend_per_capita
1/2 até 1 SM                           rend_per_capita
1 até 2 SM                             rend_per_capita
2 até 3 SM                             rend_per_capita
Mais de 3 SM                           rend_per_capita
18 a 24 anos                           fx_idade_s     
25 a 29 anos                           fx_idade_s     
30 a 39 anos                           fx_idade_s     
40 anos ou mais                        fx_idade_s     
urbano                                 urb_rur        
rural                                  urb_rur        
Rondônia                               uf             
Acre                                   uf             
Amazonas                               uf             
Roraima                                uf             
Pará                                   uf             
Amapá                                  uf             
Tocantins                              uf             
Maranhão                               uf             
Piauí                                  uf             
Ceará                                  uf             
Rio Grande do Norte                    uf             
Paraíba                                uf             
Pernambuco                             uf             
Alagoas                                uf             
Sergipe                                uf             
Bahia                                  uf             
⋮                                      ⋮              
Rio Branco3                            capital        
Manaus3                                capital        
Boa Vista3                             capital        
Belém3                                 capital        
Macapá3                                capital        
Palmas3                                capital        
São Luís3                              capital        
Teresina3                              capital        
Fortaleza3                             capital        
Natal3                                 capital        
João Pessoa3                           capital        
Recife3                                capital        
Maceió3                                capital        
Aracaju3                               capital        
Salvador3                              capital        
Belo Horizonte3                        capital        
Vitória3                               capital        
Rio de Janeiro7                        capital        
São Paulo6                             capital        
Curitiba3                              capital        
Florianópolis3                         capital        
Porto Alegre3                          capital        
Campo Grande3                          capital        
Cuiabá3                                capital        
Goiânia3                               capital        
Brasília3                              capital        
Fundamental incompleto ou equivalente3 gescol         
Médio incompleto ou equivalente3       gescol         
Superior incompleto ou equivalente3    gescol         
Superior completo3                     gescol         
                                       abr_nome                             
Branca                                 Branca                               
Preta                                  Preta                                
Parda                                  Parda                                
Até 1/2 SM                             Até 1/2 SM                           
1/2 até 1 SM                           1/2 até 1 SM                         
1 até 2 SM                             1 até 2 SM                           
2 até 3 SM                             2 até 3 SM                           
Mais de 3 SM 

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [21]:
matriz_totais <- popula_indicadores(design_por_abrangencia, totais, indicadores, Ano, "total")

In [22]:
matriz_totais

abr_tipo abr_nome Ano  Indicador Sim       LowerS    UpperS   
S016PSim  total    Brasil   2019 S016P     0.8936008 0.8767389 0.9104627
S016PSim1 total    Capital  2019 S016P     0.8709017 0.8300706 0.9117328
S017PSim  total    Brasil   2019 S017P     0.8731066 0.8539498 0.8922634
S017PSim1 total    Capital  2019 S017P     0.8488005 0.8054984 0.8921025
S018PSim  total    Brasil   2019 S018P     0.8320475 0.8093523 0.8547428
S018PSim1 total    Capital  2019 S018P     0.8717783 0.8414178 0.9021387
S019PSim  total    Brasil   2019 S019P     0.8731421 0.8528793 0.8934049
S019PSim1 total    Capital  2019 S019P     0.9094361 0.8822897 0.9365825
          cvS       
S016PSim  0.00962753
S016PSim1 0.02392071
S017PSim  0.01119456
S017PSim1 0.02602884
S018PSim  0.01391678
S018PSim1 0.01776864
S019PSim  0.01184042
S019PSim1 0.01522971

#### Unindo tabela de indicadores e de totais

In [23]:
matriz_final <-rbind(matriz_indicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [24]:
matriz_final

abr_tipo       
Branca                                 raça           
Preta                                  raça           
Parda                                  raça           
Até 1/2 SM                             rend_per_capita
1/2 até 1 SM                           rend_per_capita
1 até 2 SM                             rend_per_capita
2 até 3 SM                             rend_per_capita
Mais de 3 SM                           rend_per_capita
18 a 24 anos                           fx_idade_s     
25 a 29 anos                           fx_idade_s     
30 a 39 anos                           fx_idade_s     
40 anos ou mais                        fx_idade_s     
urbano                                 urb_rur        
rural                                  urb_rur        
Rondônia                               uf             
Acre                                   uf             
Amazonas                               uf             
Roraima                                uf             
Pará                                   uf             
Amapá                                  uf             
Tocantins                              uf             
Maranhão                               uf             
Piauí                                  uf             
Ceará                                  uf             
Rio Grande do Norte                    uf             
Paraíba                                uf             
Pernambuco                             uf             
Alagoas                                uf             
Sergipe                                uf             
Bahia                                  uf             
⋮                                      ⋮              
Fortaleza3                             capital        
Natal3                                 capital        
João Pessoa3                           capital        
Recife3                                capital        
Maceió3                                capital        
Aracaju3                               capital        
Salvador3                              capital        
Belo Horizonte3                        capital        
Vitória3                               capital        
Rio de Janeiro7                        capital        
São Paulo6                             capital        
Curitiba3                              capital        
Florianópolis3                         capital        
Porto Alegre3                          capital        
Campo Grande3                          capital        
Cuiabá3                                capital        
Goiânia3                               capital        
Brasília3                              capital        
Fundamental incompleto ou equivalente3 gescol         
Médio incompleto ou equivalente3       gescol         
Superior incompleto ou equivalente3    gescol         
Superior completo3                     gescol         
S016PSim                               total          
S016PSim1                              total          
S017PSim                               total          
S017PSim1                              total          
S018PSim                               total          
S018PSim1                              total          
S019PSim                               total          
S019PSim1                              total          
                                       abr_nome                             
Branca                                 Branca                               
Preta                                  Preta                                
Parda                                  Parda                                
Até 1/2 SM                             Até 1/2 SM                           
1/2 até 1 SM                           1/2 até 1 SM                         
1 até 2 SM                             1 até 2 SM                           
2 até 3 SM                             2 até 3 SM                           
Mais de 3 SM 

#### Exportando tabela de indicadores calculados - Módulo S 2019

In [26]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2019S_R.csv"),sep = ";",dec = ",",row.names = FALSE)